In [1]:
import numpy as np 
import pandas as pd 
import altair as alt 
import os 
import re 
import ntpath
from Commons.data_processing import *
from Commons.DataProcessors.pd_processor import PDProcessor

In [2]:
files = get_files(r".\N_Glycosylation_Results")

In [3]:
read_data = None

for file in files:

    base_name, _ = ntpath.splitext(ntpath.basename(file))
    div = base_name.split("-")[0]
    div = div.split("_")
    conc, temp, run = div[-3:]

    data = PDProcessor([file], sample_name="_".join(div[-3:]))
    data.add_special_column("concentration", conc)
    data.add_special_column("temperature", temp)
    data.add_special_column("run", run)

    if read_data is None:
        read_data = data
    else:
        read_data.join_processors(data)


read_data.alias_engine("")


In [163]:
peptides = read_data.peptides[~read_data.peptides.glycan_composition.isna()]

conc_map = {"1": 1.0, "05": 0.5, "025": 0.25, "0125": 0.125, "00625": 0.0625}
peptides.loc[:, 'concentration'] = peptides.concentration.map(conc_map)


C:\Users\graha\AppData\Roaming\Python\Python38\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
<ipython-input-163-8c70d0a7fce1>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  peptides.loc[:, 'concentration'] = peptides.concentration.map(conc_map)


In [164]:
cutoffs = [50, 100, 150, 200, 250, 300, 350, 400, 500]
nums = []
for cut in cutoffs:
    nums.append(len(peptides[peptides.byonic_score >= cut]))

res = pd.DataFrame({"cutoffs": cutoffs, "vals": nums})

alt.Chart(res).mark_bar().encode(x="cutoffs:N", y="vals:Q")

alt.Chart(...)

In [165]:
peptides = peptides[peptides.byonic_score >= 300]
peptides['glycan'] = peptides.glycan_composition

In [166]:
def categorize_glycan(glycan):

    glycan = glycan.replace(")", ",")
    glycan = glycan.replace("(", " ")
    glycan = glycan.split(",")[:-1]
    d = {k: int(v) for [k, v] in [i.split(" ") for i in glycan]}

    if "NeuAc" in d or "NeuGc" in d:
        return "Sialylated"
    elif "Fuc" in d:
        if d["HexNAc"] > 2:
            return "Fucosylated"
        elif d["HexNAc"] == 2:
            if "Hex" in d:
                if d["Hex"] > 4:
                    return "Complex"
            else:
                return "Paucimannose"
    elif d["HexNAc"] > 2:
        return "Complex"
    elif d["HexNAc"] <= 2:
        if "Hex" in d:
            if d["Hex"] <= 9 and d["Hex"] > 4:
                return "High Mannose"

        return "Paucimannose"

def determine_degree_sial(glycan):

    degree_map = {
        1: 'Monosialylated',
        2: 'Disialylated',
        3: 'Trisialylated',
        4: 'Tetrasialylated',
        5: 'Pentasialylated',
    }

    glycan = glycan.replace(')', ',')
    glycan = glycan.replace('(', ' ')
    glycan = glycan.split(',')[:-1]
    d = {k:int(v) for [k, v] in [i.split(' ') for i in glycan]}

    if not 'NeuAc' in d and 'NeuGc' not in d:
        return 0
    else:
        total = int(d.get('NeuAc', 0)) + int(d.get('NeuGc', 0))
        return degree_map[total]


peptides.loc[:, "glycan_type"] = peptides.glycan.map(categorize_glycan)
peptides.loc[:, "degree_sial"] = peptides.glycan.map(determine_degree_sial)


In [167]:
# map unique glycopeptide id

peptides.loc[:, "pep_mods"] = peptides.apply(
    lambda x: x["sequence"] + "_" + x["modifications"], axis=1
)
peptides = peptides.reset_index()
peptides = peptides.sort_values('concentration', ascending=False)
peptides.head(3)


index accession                                        description  \
2475    423    P61823  Ribonuclease pancreatic OS=Bos taurus OX=9913 ...   
2007    277    P61823  Ribonuclease pancreatic OS=Bos taurus OX=9913 ...   
2015    306    P61823  Ribonuclease pancreatic OS=Bos taurus OX=9913 ...   

     checked confidence                   annotated_sequence  \
2475    True       High                       [K].SRNLTK.[D]   
2007    True       High                       [R].NLTKDR.[C]   
2015    True        Low  [R].QHMDSSTSAASSSNYCNQMMKSRNLTK.[D]   

                                          modifications num_protein_groups  \
2475                             1xHexNAc(2)Hex(8) [N3]                  1   
2007                                   1xHexNAc(1) [N1]                  1   
2015  1xCarbamidomethyl [C16]; 1xDeamidated [Q18]; 1...                  1   

     num_proteins num_psms master_protein_accessions  \
2475            1        7                    P61823   
2007            1        2                    P61823   
2015            1        1                    P61823   

     positions_in_master_proteins modifications_in_master_proteins  \
2475               P61823 [58-63]                              NaN   
2007               P61823 [60-65]                              NaN   
2015               P61823 [37-63]                              NaN   

     num_missed_cleavages theo_mh+_da glycan_composition off_by_x  \
2475                    1        2421    HexNAc(2)Hex(8)        0   
2007                    1     949.495          HexNAc(1)        0   
2015                    2     4728.93    HexNAc(5)Hex(4)        1   

     position_in_protein confidence log_prob byonic_score delta_byonic_score  \
2475                  58       High      2.1        441.2               85.1   
2007                  60       High     3.25        500.2              334.3   
2015                  37        Low     3.56        300.9              300.9   

     delta_mod_score       pep_2d   q_value_2d      fdr_2d  \
2475            85.1   0.00794231   0.00364963  0.00358744   
2007           334.3  0.000563114  4.92578e-05           0   
2015               0  0.000276334  3.00626e-05           0   

     peptide_group_fdr_2d       pep_1d   q_value_1d      fdr_1d  \
2475            0.0185185    0.0102316   0.00378429  0.00358744   
2007                    0  0.000912654  7.98408e-05           0   
2015                    0  0.000447899  4.87292e-05           0   

     peptide_group_fdr_1d              sequence_in_protein  \
2475            0.0185185                       K.SRNLTK.D   
2007                    0                       R.NLTKDR.C   
2015                    0  R.QHMDSSTSAASSSNYCNQMMKSRNLTK.D   

     positions_in_proteins                     sequence data_source  \
2475               [58-63]                       SRNLTK  1_60C_Run3   
2007               [60-65]                       NLTKDR  1_30C_Run3   
2015               [37-63]  QHMDSSTSAASSSNYCNQMMKSRNLTK  1_30C_Run3   

     concentration temperature   run           glycan   glycan_type  \
2475             1         60C  Run3  HexNAc(2)Hex(8)  High Mannose   
2007             1         30C  Run3        HexNAc(1)  Paucimannose   
2015             1         30C  Run3  HexNAc(5)Hex(4)       Complex   

     degree_sial                                           pep_mods  
2475           0                      SRNLTK_1xHexNAc(2)Hex(8) [N3]  
2007           0                            NLTKDR_1xHexNAc(1) [N1]  
2015           0  QHMDSSTSAASSSNYCNQMMKSRNLTK_1xCarbamidomethyl ...

In [168]:
peptides[peptides.degree_sial == 'Pentasialylated']

index accession                                        description  \
1208    224    P12763  Alpha-2-HS-glycoprotein OS=Bos taurus OX=9913 ...   

     checked confidence       annotated_sequence  \
1208    True       High  [K].LCPDCPLLAPLNDSR.[V]   

                                          modifications num_protein_groups  \
1208  2xCarbamidomethyl [C2; C5]; 1xHexNAc(5)Hex(6)F...                  1   

     num_proteins num_psms master_protein_accessions  \
1208            1        1                    P12763   

     positions_in_master_proteins modifications_in_master_proteins  \
1208             P12763 [145-159]                              NaN   

     num_missed_cleavages theo_mh+_da             glycan_composition off_by_x  \
1208                    0     5330.09  HexNAc(5)Hex(6)Fuc(1)NeuAc(5)       -1   

     position_in_protein confidence log_prob byonic_score delta_byonic_score  \
1208                 145       High     4.65        391.4              391.4   

     delta_mod_score       pep_2d   q_value_2d fdr_2d peptide_group_fdr_2d  \
1208           391.4  2.22881e-05  3.05337e-06      0                    0   

           pep_1d   q_value_1d fdr_1d peptide_group_fdr_1d  \
1208  3.30893e-05  4.52185e-06      0                    0   

      sequence_in_protein positions_in_proteins         sequence  data_source  \
1208  K.LCPDCPLLAPLNDSR.V             [145-159]  LCPDCPLLAPLNDSR  05_30C_Run1   

     concentration temperature   run                         glycan  \
1208           0.5         30C  Run1  HexNAc(5)Hex(6)Fuc(1)NeuAc(5)   

     glycan_type      degree_sial  \
1208  Sialylated  Pentasialylated   

                                               pep_mods  
1208  LCPDCPLLAPLNDSR_2xCarbamidomethyl [C2; C5]; 1x...

# What are we even doing?

`Intact Glycopeptide Analysis at Elevated Temperatures Reveals limitations and Considerations in Label Free Quantitation`

1. We know that different temperatures enable different levels of performance in glycopeptide identification
- Show the difference between temperatures (num glycopeptideP)
- Pinopint what is responsible. Increased peak area? Peak intensity? Is the separation of isomers somehow causing identification errors?

2. Is this a global occurrence or are various glycan types affected differently?
- For each temperature and glycan types, show the relative identification rates
- Using the pinpointed cause of different performance from aim1, show positive and negative examples for glycan types.

3. How does this effect quantitation?
- Is LFQ even remotely possible when temperature is varied?
- Is the ability to do LFQ rescued when analyzing at one temperature?
- Can we achieve greater LOQ when running at the optimal temperature?
- Are there any glycan types that show no ability to do LFQ?
- Is there a method of LFQ that is more useful than the other?

## 1a

Taking the max concentration, what is the difference between temperature?

In [169]:
# information to extract: num peptides, num unique glycans, num unique peptide backbones
temps, vals, kind, concent = [], [], [], []

for conc in peptides.concentration.unique():
    head = peptides[peptides.concentration == conc]

    for temp in head.temperature.unique():
        body = head[head.temperature==temp]

        for run in body.run.unique():
            tail = body[body.run == run]

            unique_gly = len(tail.pep_mods.unique())
            concent.append(conc)
            vals.append(unique_gly)
            temps.append(temp)
            kind.append("Unique Glycopeptides")

            unique_seq = len(tail.sequence.unique())
            concent.append(conc)
            vals.append(unique_seq)
            temps.append(temp)
            kind.append("Unique Backbones")

            unique_glycans = len(tail.glycan.unique())
            concent.append(conc)
            vals.append(unique_glycans)
            temps.append(temp)
            kind.append("Unique Glycans")

res = pd.DataFrame({"Temperature": temps, "Kind": kind, "Values": vals, "Concentration": concent})

my_colors = alt.Color(
    "Temperature:N",
    scale=alt.Scale(
        domain=["30C", "45C", "60C"], range=["#6E6581", "#B0B2BB", "#6B8A97"]
    ),
)

conc_max_comparison = (
    alt.Chart(res)
    .mark_bar()
    .encode(
        x=alt.X("Temperature:N", axis=alt.Axis(labelAngle=-45)),
        y=alt.Y("mean(Values):Q", title="Number of Identifications"),
        color=my_colors
    )
).properties(
    width=75,
    height=75
)

cmc_err_bars = (
    alt.Chart(res)
    .mark_errorbar(extent='stdev')
    .encode(
        x=alt.X("Temperature:N", title="", axis=alt.Axis(labelAngle=-45)),
        y=alt.Y("mean(Values):Q", title=""),
    )
)

base = alt.layer(conc_max_comparison, cmc_err_bars).facet(
    column="Kind:N", spacing=50,
)

max_conc = base.transform_filter(
        alt.datum.Concentration == 1.0
    ).properties(
        title='Temperature Differences, Max Concentration'
    )


all_conc = alt.vconcat()
for concentration in res.Concentration.unique():
    all_conc &= base.transform_filter(alt.datum.Concentration==concentration).properties(title=f'Concentration = {concentration}')


In [170]:
all_conc

alt.VConcatChart(...)

# Observations
When comparing across temperatures, there is often a slight difference in number of identifications between 30C and 45C. However, this difference is small and shows no consistent trend between concentrations analyzed.

However, at all concentrations tested, their is a significant difference when running at 60C. What could be causing this?



## 1b

What is a main source of this difference?

## 2a

Do all glycan types experience this trend?

In [171]:
glycan_sub = peptides[
    [
        "sequence",
        "glycan",
        "glycan_type",
        "pep_mods",
        "temperature",
        "concentration",
        "run",
    ]
]

glycan_color_scale = alt.Scale(
    domain=[
        'Sialylated',
        'Fucosylated',
        'Complex',
        'Paucimannose',
        'High Mannose',
    ],
    range=[
        '#6E6581',
        '#AF3A53',
        '#6B8A97',
        '#B0B2BB',
        '#658A64',
    ]
)

bars = (
    alt.Chart(glycan_sub)
    .mark_bar()
    .encode(
        x=alt.X("temperature:N", title="", axis=alt.Axis(labelAngle=-45)),
        y=alt.Y("mean(my_count):Q", title="Number Glycan Matches"),
        color=alt.Color("glycan_type:N", scale=glycan_color_scale),
    )
    .transform_aggregate(
        my_count='count(glycan_type)',
        groupby=['glycan_type', 'concentration', 'temperature', 'run']
    )
)

err = (
    alt.Chart(glycan_sub)
    .mark_errorbar(extent='stdev')
    .encode(
        x=alt.X("temperature:N", title="", axis=alt.Axis(labelAngle=-45)),
        y=alt.Y("mean(my_count):Q", title="Number Glycan Matches"),
    )
    .transform_aggregate(
        my_count='count(glycan_type)',
        groupby=['glycan_type', 'concentration', 'temperature', 'run']
    )
)

glyc_by_concentration = alt.layer(bars, err).facet(
    column=alt.Column('glycan_type', title=''),
    row='concentration:N'
)

conc_bars = alt.vconcat()
for concentration in glycan_sub.concentration.unique():
    conc_bars &= base.transform_filter(alt.datum.concentration == concentration).properties(
        title=f"Concentration = {concentration}"
    )
conc_bars.configure_concat(
    spacing=50
)

glyc_by_concentration

alt.FacetChart(...)

At all concentrations, complex and sialylated glycopeptides show decreasing numbers of positive identifications as temperature increases. Fucosylated and High mannose glycopeptides follow this trend at greater dilutions but resist at higher analyte concentrations. In general, we see an increase in the number of paucimannose identifications -- could we be promoting premature glycan dissociation at higher temperatures? However, the number of paucimannose glycopepitdes gained (<5) as temperature increases does not match the number of glycopeptides lost in other categories, so it is unlikely the sole cause of decreased identifications is premature dissociation.

What could be other causes? 

- Reduced peak area causing them to not be selected? (check for mass in ms1 but not in ms2)

- Poor fragmentation efficiency? (Compare MS2 from positive and negative runs) I evaluated this briefly in the ABC manuscript, temp didn't seem to effect it.

- ## <b> Could we be seeing a change in number of sialic acids as temp changes?? </b>

## 2b

Let's investigate if the number of PSMs or peak area could show us why this is happening.

In [172]:
psms = read_data.psms[(read_data.psms.byonic_score >= 200) & (~read_data.psms.glycan_composition.isna())]
psms.loc[:, 'concentration'] = psms.concentration.map(conc_map)
psms.loc[:, 'glycan'] = psms.glycan_composition.map(categorize_glycan)
psms = psms.sort_values('concentration', ascending=False)

psms.loc[:, "pep_mods"] = psms.apply(
    lambda x: x["sequence"] + "_" + x["modifications"], axis=1
)

psms = psms.reset_index()

C:\Users\graha\AppData\Roaming\Python\Python38\site-packages\pandas\core\indexing.py:1048: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item_labels[indexer[info_axis]]] = value
C:\Users\graha\AppData\Roaming\Python\Python38\site-packages\pandas\core\indexing.py:845: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
C:\Users\graha\AppData\Roaming\Python\Python38\site-packages\pandas\core\indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a 

In [173]:
spec_count = psms[
    ["sequence", "glycan", "temperature", "concentration", "run", "pep_mods"]
]

boxes = (
    alt.Chart(spec_count)
    .mark_boxplot()
    .encode(
        x=alt.X("temperature:N",
                axis=alt.Axis(labelAngle=-45)),
        y="my_count:Q",
        color=alt.Color("glycan:N", scale=glycan_color_scale),
    )
    .transform_aggregate(
        my_count="count(pep_mods)",
        groupby=["temperature", "run", "concentration", "glycan"],
    )
)

conc_boxes = alt.vconcat()
for concentration in spec_count.concentration.unique():
    conc_boxes &= boxes.transform_filter(
        alt.datum.concentration == concentration
    ).properties(title=f"Concentration = {concentration}")

test = alt.layer(boxes).facet(
    column=alt.Column('glycan:N', title=''),
    row=alt.Row('concentration:N', title='')
)

In [174]:
glyc_by_concentration | test

alt.HConcatChart(...)

In [175]:
test = peptides[
    [
        "sequence",
        "glycan",
        "glycan_type",
        "pep_mods",
        "temperature",
        "concentration",
        "run",
        "degree_sial",
    ]
]

sial = alt.Chart(test[test.degree_sial != 0]).mark_bar().encode(
    x=alt.X(
        "temperature:N",
        title="",
        axis=alt.Axis(labelAngle=-45)
    ),
    y=alt.Y("mean(my_count):Q"),
    color='degree_sial:N'
).transform_aggregate(
    my_count = 'count(degree_sial):Q',
    groupby = ['temperature', 'run', 'concentration', 'degree_sial']
)

alt.layer(sial).facet(
    column=alt.Column('degree_sial:O'),
    row=alt.Row('concentration:Q')
)

alt.FacetChart(...)

## Possible Observation

When looking at glycan types across all concentrations and temperatures, the only types that resist the trend of decreasing in accordance with temperature is paucimannose and sialylated. However, if we consider the degree of sialylation, this does follow the trend of decreasing as temperature increases. 

How can we verify or check to see if this is indeed the case.

### Look for instances where a glycopeptide is identified at 30C and not 45C. Then see if at the same retention time we see a new/different glycan attached to the same backbone.

In [177]:
test_conc = psms[psms.concentration==0.5]
test_30 = test_conc[test_conc.temperature=="30C"]
test_45 = test_conc[test_conc.temperature=="45C"]

x = set(test_30.pep_mods.tolist()) - set(test_45.pep_mods.tolist())
y = set(test_45.pep_mods.tolist()) - set(test_30.pep_mods.tolist())

In [181]:
pd.set_option('max_rows', 5)
test_30[test_30.pep_mods.isin(x)]

index accession                                        description  \
5600   1630    P61823  Ribonuclease pancreatic OS=Bos taurus OX=9913 ...   
5704    864    Q3SZR3  Alpha-1-acid glycoprotein OS=Bos taurus OX=991...   
...     ...       ...                                                ...   
8537   1913    P61823  Ribonuclease pancreatic OS=Bos taurus OX=9913 ...   
8551   1883    P61823  Ribonuclease pancreatic OS=Bos taurus OX=9913 ...   

     checked confidence identifying_node psm_ambiguity annotated_sequence  \
5600    True     Medium  PMI-Byonic (A4)   Unambiguous     [K].SRnLTK.[D]   
5704    True     Medium  PMI-Byonic (A4)   Unambiguous    [R].QnGTLSK.[V]   
...      ...        ...              ...           ...                ...   
8537    True       High  PMI-Byonic (A4)   Unambiguous       [R].nLTK.[D]   
8551    True     Medium  PMI-Byonic (A4)   Unambiguous       [R].nLTK.[D]   

                  modifications num_proteins master_protein_accessions  \
5600  N3(HexNAc(2)Hex(5)Fuc(1))            1                    P61823   
5704  N2(HexNAc(5)Hex(5)Fuc(1))            1                    Q3SZR3   
...                         ...          ...                       ...   
8537        N1(HexNAc(4)Hex(5))            1                    P61823   
8551  N1(HexNAc(2)Hex(5)Fuc(1))            1                    P61823   

     protein_accessions num_missed_cleavages charge deltascore deltacn rank  \
5600             P61823                    1      2          1       0    1   
5704             Q3SZR3                    0      2          1       0    1   
...                 ...                  ...    ...        ...     ...  ...   
8537             P61823                    0      2          1       0    1   
8551             P61823                    0      2          1       0    1   

     search_engine_rank   m/z_da   mh+_da theo_mh+_da deltam_ppm deltam/z_da  \
5600                  1  1040.96  2080.91      2080.9       3.77     0.00392   
5704                  1  1360.05   2719.1     2719.12      -7.44    -0.01012   
...                 ...      ...      ...         ...        ...         ...   
8537                  1  1049.44  2097.87     2097.87      -0.65    -0.00068   
8551                  1  919.374  1837.74     1837.77     -15.42    -0.01416   

                               activation_type nce_percent ms_order  \
5600  HCD (High Energy Collision Dissociation)          30      MS2   
5704  HCD (High Energy Collision Dissociation)          30      MS2   
...                                        ...         ...      ...   
8537  HCD (High Energy Collision Dissociation)          30      MS2   
8551  HCD (High Energy Collision Dissociation)          30      MS2   

     isolation_interference_percent ion_inject_time_ms   rt_min first_scan  \
5600                              0                150  20.6685       7832   
5704                        29.0975                150  31.1619      11716   
...                             ...                ...      ...        ...   
8537                              0                150  16.5653       6271   
8551                              0                150  15.4049       5825   

                         spectrum_file file_id log_prob byonic_score  \
5600  20210710_GlycEnr_05_30C_Run3.raw     F12     0.42        211.2   
5704  20210710_GlycEnr_05_30C_Run3.raw     F12     0.43        226.7   
...                                ...     ...      ...          ...   
8537  20210710_GlycEnr_05_30C_Run2.raw     F11     1.93        233.1   
8551  20210710_GlycEnr_05_30C_Run2.raw     F11     0.57        227.6   

     delta_byonic_score delta_mod_score     pep_2d  q_value_2d      fdr_2d  \
5600               38.1            38.1   0.377515   0.0391837   0.0357942   
5704              226.7           226.7   0.370537   0.0391837   0.0385852   
...                 ...             ...        ...         ...         ...   
8537              233.1           233.1  0.0